In [5]:
!pip install pandas

     ---------------------------------------- 0.0/11.6 MB ? eta -:--:--
     ---------------------------------------- 0.0/11.6 MB 2.0 MB/s eta 0:00:06
     ---------------------------------------- 0.0/11.6 MB 2.0 MB/s eta 0:00:06
      --------------------------------------- 0.2/11.6 MB 1.5 MB/s eta 0:00:08
      --------------------------------------- 0.2/11.6 MB 1.3 MB/s eta 0:00:10
      --------------------------------------- 0.3/11.6 MB 1.2 MB/s eta 0:00:10
     - -------------------------------------- 0.4/11.6 MB 1.4 MB/s eta 0:00:08
     - -------------------------------------- 0.4/11.6 MB 1.3 MB/s eta 0:00:09
     - -------------------------------------- 0.5/11.6 MB 1.5 MB/s eta 0:00:08
     - -------------------------------------- 0.6/11.6 MB 1.4 MB/s eta 0:00:08
     -- ------------------------------------- 0.6/11.6 MB 1.4 MB/s eta 0:00:08
     -- ------------------------------------- 0.6/11.6 MB 1.3 MB/s eta 0:00:09
     -- ------------------------------------- 0.7/11.6 MB 1


[notice] A new release of pip is available: 23.0.1 -> 25.0.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
import h5py

file_path = "E:/Major Project/Data/chunk1/chunk1.hdf5"
hdf5_file = h5py.File(file_path, 'r')
print(len(hdf5_file["data"].keys()))
hdf5_file["data"].keys()

235426


<KeysViewHDF5 ['109C.TA_201510210555_NO', '109C.TA_201511061450_NO', '109C.TA_201511070220_NO', '109C.TA_201511140515_NO', '109C.TA_201512251850_NO', '109C.TA_201512302245_NO', '109C.TA_201601031820_NO', '109C.TA_201601060025_NO', '109C.TA_201601150401_NO', '109C.TA_201602260731_NO', '109C.TA_201603041044_NO', '109C.TA_201603110142_NO', '109C.TA_201603151723_NO', '109C.TA_201603252003_NO', '109C.TA_201604180846_NO', '109C.TA_201604231547_NO', '109C.TA_201605040518_NO', '109C.TA_201605190224_NO', '109C.TA_201605260424_NO', '109C.TA_201605302234_NO', '109C.TA_201606170250_NO', '109C.TA_201606191044_NO', '109C.TA_201606301449_NO', '109C.TA_201607051916_NO', '109C.TA_201607130559_NO', '109C.TA_201607260634_NO', '109C.TA_201607291655_NO', '109C.TA_201608010625_NO', '109C.TA_201609190936_NO', '109C.TA_201610090308_NO', '109C.TA_201610181309_NO', '109C.TA_201610231854_NO', '109C.TA_201610291226_NO', '109C.TA_201611051419_NO', '109C.TA_201611162142_NO', '109C.TA_201611192251_NO', '109C.TA_2016

In [7]:
import numpy as np

# Get the data
# earthquake_data = np.load(r'E:\Major Project\Data\Split\X_test.npy')
earthquake_data.shape

(12728, 6000, 3)

In [8]:
import numpy as np
import h5py
import random

# Extract all dataset names (waveforms)
dataset_names = list(hdf5_file["data"].keys())

# Randomly select 20,000 dataset names
selected_datasets = random.sample(dataset_names, 20000)

# Load selected waveforms
noise_waveforms = []
for dataset_name in selected_datasets:
    dataset = np.array(hdf5_file["data"][dataset_name])  # Shape: (1000, 3)
    noise_waveforms.append(dataset)

# Convert to NumPy array
classifier_X_train = np.array(noise_waveforms)  # Shape: (20000, 1000, 3)

# Save the dataset
np.save("classifier_X_train.npy", classifier_X_train)

print("✅ classifier_X_train.npy saved! Shape:", classifier_X_train.shape)

# Close the file
hdf5_file.close()


✅ classifier_X_train.npy saved! Shape: (20000, 6000, 3)


In [10]:
import numpy as np
from sklearn.model_selection import train_test_split

# Load noise data (already (20000, 1000, 3))
X_noise = np.load(r"E:\Major Project\Data\Classifier Data\classifier_X_train.npy")  
y_noise = np.zeros(len(X_noise))  # Label = 0 (Noise)

# Load earthquake data and extract first 1000 timesteps
X_earthquake = earthquake_data[:, :1000, :]  # Shape: (12728, 1000, 3)
y_earthquake = np.ones(len(X_earthquake))  # Label = 1 (Earthquake)

# Combine both datasets
X = np.vstack([X_noise[:, :1000, :], X_earthquake])
y = np.hstack([y_noise, y_earthquake])

# Split into train & test sets (80% train, 20% test)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42, stratify=y)
save_dir = r"E:\Major Project\Data\Classifier Data"

# Save the datasets
np.save(save_dir + "/X_train_c.npy", X_train)
np.save(save_dir + "/X_test_c.npy", X_test)
np.save(save_dir + "/y_train_c.npy", y_train)
np.save(save_dir + "/y_test_c.npy", y_test)

print(f"✅ Dataset prepared! Train: {X_train.shape}, Test: {X_test.shape}")


✅ Dataset prepared! Train: (26182, 1000, 3), Test: (6546, 1000, 3)


In [ ]:
import numpy as np
import joblib
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score
from sklearn.model_selection import train_test_split

# Load dataset
# X_train = np.load("X_train.npy")  # Shape: (26182, 1000, 3)
# X_test = np.load("X_test.npy")    # Shape: (6546, 1000, 3)
# y_train = np.load("y_train.npy")  # Shape: (26182,)
# y_test = np.load("y_test.npy")    # Shape: (6546,)

# Flatten input for Random Forest (Convert 3D → 2D)
X_train = X_train.reshape(X_train.shape[0], -1)  # Shape: (26182, 3000)
X_test = X_test.reshape(X_test.shape[0], -1)     # Shape: (6546, 3000)

# Define Random Forest model
clf = RandomForestClassifier(n_estimators=100, random_state=42, n_jobs=-1)
clf.fit(X_train, y_train)

# Save trained model
joblib.dump(clf, "random_forest_model.pkl")
print("✅ Model saved as 'random_forest_model.pkl'!")

# Predictions
y_pred = clf.predict(X_test)

# Evaluation Metrics
accuracy = accuracy_score(y_test, y_pred)
precision = precision_score(y_test, y_pred)
recall = recall_score(y_test, y_pred)
f1 = f1_score(y_test, y_pred)
 
# Print results
print(f"✅ Accuracy: {accuracy:.4f}")
print(f"✅ Precision: {precision:.4f}")
print(f"✅ Recall: {recall:.4f}")
print(f"✅ F1 Score: {f1:.4f}")


✅ Model saved as 'random_forest_model.pkl'!
✅ Accuracy: 0.9994
✅ Precision: 0.9996
✅ Recall: 0.9988
✅ F1 Score: 0.9992
